In [1]:
import pandas as pd
import numpy as np
from datetime import datetime, timezone
from shapely.geometry import Point
import requests
import osmnx as ox
from math import radians, sin, cos, sqrt, atan2

class RouteFeatureExtractor:
    """
    Extracts OSM, weather and geometric features from a GPS route.
    Features are aggregated into fixed-length segments.
    """

    # INIT
    def __init__(self, gps_route, weather_api_key=None):

        self.weather_api_key = weather_api_key

        self.df = pd.DataFrame(gps_route, columns=["lat", "lon"])
        self.df["Hour"] = datetime.now(timezone.utc).hour

        # Distances
        self.df["Delta_d"] = 0.0          # will become per-segment delta
        self.df["Trip_distance"] = 0.0    # cumulative [m]

        # Continuous
        self.df["Hum"] = np.nan
        self.df["Slope"] = 0.0

        # OSM binary features
        self.df["primary"] = 0
        self.df["residential"] = 0
        self.df["secondary"] = 0
        self.df["crossing"] = 0
        self.df["tertiary"] = 0
        self.df["give_way"] = 0

    # HAVERSINE
    def _haversine_m(self, p1, p2):
        R = 6371000.0
        lat1, lon1 = radians(p1[0]), radians(p1[1])
        lat2, lon2 = radians(p2[0]), radians(p2[1])

        dlat = lat2 - lat1
        dlon = lon2 - lon1

        a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
        return 2 * R * atan2(sqrt(a), sqrt(1 - a))

    # DISTANCES
    def compute_distances(self):

        deltas = [0.0]

        for i in range(1, len(self.df)):
            p1 = self.df.loc[i - 1, ["lat", "lon"]].values
            p2 = self.df.loc[i, ["lat", "lon"]].values
            deltas.append(self._haversine_m(p1, p2))

        self.df["Delta_d"] = deltas
        self.df["Trip_distance"] = np.cumsum(deltas)

    # SEGMENTATION (ACCUMULATED)
    def assign_segments(self, segment_length_m=100):

        segment_ids = []
        current_segment = 0
        acc_dist = 0.0

        for i, d in enumerate(self.df["Delta_d"]):

            if i == 0:
                segment_ids.append(0)
                continue

            acc_dist += d

            if acc_dist >= segment_length_m:
                current_segment += 1
                acc_dist = 0.0

            segment_ids.append(current_segment)

        self.df["segment_id"] = segment_ids

    # DELTA_D PER SEGMENT (difference between segments)
    def compute_delta_d_per_segment(self):

        seg_lengths = (
            self.df
            .groupby("segment_id")["Delta_d"]
            .sum()
            .reset_index(name="segment_length")
        )

        seg_lengths["cum_dist"] = seg_lengths["segment_length"].cumsum()
        seg_lengths["Delta_d"] = seg_lengths["cum_dist"].diff()
        seg_lengths.loc[0, "Delta_d"] = 0.0

        delta_map = dict(
            zip(seg_lengths["segment_id"], seg_lengths["Delta_d"])
        )

        self.df["Delta_d"] = self.df["segment_id"].map(delta_map)

    # WEATHER (constant per trip → aggregated later)
    def fetch_weather(self):

        if self.weather_api_key is None:
            return

        try:
            lat, lon = self.df.loc[0, ["lat", "lon"]]

            r = requests.get(
                "https://api.worldweatheronline.com/premium/v1/past-weather.ashx",
                params={
                    "key": self.weather_api_key,
                    "q": f"{lat},{lon}",
                    "format": "json",
                    "date": datetime.now(timezone.utc).strftime("%Y-%m-%d"),
                    "tp": 24,
                },
                timeout=10
            )
            r.raise_for_status()

            hum = float(r.json()["data"]["weather"][0]["hourly"][0]["humidity"])
            self.df["Hum"] = hum

        except Exception as e:
            print("Weather API error:", e)

    # OSM FEATURES
    def fetch_osm_features(self):

        try:
            center = (self.df["lat"].mean(), self.df["lon"].mean())

            G = ox.graph_from_point(center, dist=1500, network_type="drive")
            nodes, edges = ox.graph_to_gdfs(G)

            utm_crs = ox.projection.project_gdf(nodes).crs
            nodes_p = nodes.to_crs(utm_crs)
            edges_p = edges.to_crs(utm_crs)

            for i, row in self.df.iterrows():

                p = Point(row["lon"], row["lat"])
                p_proj = ox.projection.project_geometry(p, to_crs=utm_crs)[0]

                edge_idx = edges_p.distance(p_proj).idxmin()
                highway = edges.loc[edge_idx].get("highway", "")

                if isinstance(highway, list):
                    highway = highway[0]

                if highway == "primary":
                    self.df.loc[i, "primary"] = 1
                elif highway == "residential":
                    self.df.loc[i, "residential"] = 1
                elif highway == "secondary":
                    self.df.loc[i, "secondary"] = 1

                node_idx = nodes_p.distance(p_proj).idxmin()
                node_hw = nodes.loc[node_idx].get("highway", "")

                if node_hw == "crossing":
                    self.df.loc[i, "crossing"] = 1
                elif node_hw == "tertiary":
                    self.df.loc[i, "tertiary"] = 1
                elif node_hw == "give_way":
                    self.df.loc[i, "give_way"] = 1

        except Exception as e:
            print("OSM extraction error:", e)

    # ELEVATION (ONLY SEGMENT EXTREMES)
    def fetch_elevation_for_segments(self):

        self.segment_elevations = {}

        for seg_id, group in self.df.groupby("segment_id"):

            p0 = group.iloc[0][["lat", "lon"]]
            p1 = group.iloc[-1][["lat", "lon"]]

            loc = f"{p0.lat},{p0.lon}|{p1.lat},{p1.lon}"

            try:
                r = requests.get(
                    "https://api.open-elevation.com/api/v1/lookup",
                    params={"locations": loc},
                    timeout=10
                )
                r.raise_for_status()

                res = r.json()["results"]

                self.segment_elevations[seg_id] = {
                    "z0": res[0]["elevation"],
                    "z1": res[1]["elevation"]
                }

            except Exception:
                self.segment_elevations[seg_id] = {"z0": np.nan, "z1": np.nan}

    # SLOPE PER SEGMENT (DEGREES)
    def compute_slope_per_segment(self):

        slopes = {}

        for seg_id, group in self.df.groupby("segment_id"):

            elev = self.segment_elevations.get(seg_id, None)
            d_seg = group["Delta_d"].iloc[0]

            if elev is None or d_seg <= 0:
                slope = 0.0
            else:
                z0, z1 = elev["z0"], elev["z1"]
                if np.isnan(z0) or np.isnan(z1):
                    slope = 0.0
                else:
                    slope = np.degrees(np.arctan((z1 - z0) / d_seg))

            slopes[seg_id] = slope

        self.df["Slope"] = self.df["segment_id"].map(slopes)

    # AGGREGATION
    def aggregate_segments(self):

        agg = {
            "Hour": "mean",
            "Trip_distance": "mean",
            "Delta_d": "mean",
            "Hum": "mean",
            "Slope": "mean",
            "primary": "max",
            "residential": "max",
            "secondary": "max",
            "crossing": "max",
            "tertiary": "max",
            "give_way": "max",
        }

        return (
            self.df
            .groupby("segment_id", as_index=False)
            .agg(agg)
        )

    # PIPELINE
    def run_all(self):

        self.compute_distances()
        self.assign_segments()
        self.compute_delta_d_per_segment()

        self.fetch_weather()
        self.fetch_osm_features()

        self.fetch_elevation_for_segments()
        self.compute_slope_per_segment()

        return self.aggregate_segments()

## Validamos con viajes de Ann Arbor

In [2]:
df = pd.read_csv('ev_data_processed.csv', low_memory=False)
df.columns = [c.lower() for c in df.columns]

required_cols = {"vehid", "trip", "matched_latitude", "matched_longitude"}
if not required_cols.issubset(df.columns):
    raise ValueError(
        f"El dataset debe contener las columnas: {required_cols}"
    )

veh_ids = sorted(df["vehid"].unique())

print("\nVehId disponibles en el dataset:")
print([int(v) for v in veh_ids])

vehid_sel = int(input("\nIngrese el VehId que desea analizar: "))

if vehid_sel not in veh_ids:
    raise ValueError("El VehId seleccionado no existe en el dataset.")

trip_ids = sorted(df.loc[df["vehid"] == vehid_sel, "trip"].unique())

print(f"\nTrips disponibles para el VehId {vehid_sel}:")
print([int(t) for t in trip_ids])

trip_sel = int(input("\nIngrese el Trip que desea analizar: "))

if trip_sel not in trip_ids:
    raise ValueError("El Trip seleccionado no existe para el VehId indicado.")

df_trip = (
    df[(df["vehid"] == vehid_sel) & (df["trip"] == trip_sel)]
    .sort_index()
)

gps_route = list(
    zip(
        df_trip["latitude"].astype(float),
        df_trip["longitude"].astype(float)
    )
)

if len(gps_route) < 2:
    raise ValueError("La ruta seleccionada no contiene suficientes puntos GPS.")

print("\nRuta GPS extraída correctamente.")
print(f"Número total de puntos GPS: {len(gps_route)}")
print(
    f"Punto inicial: "
    f"({gps_route[0][0]:.6f}, {gps_route[0][1]:.6f})"
)
print(
    f"Punto final: "
    f"({gps_route[-1][0]:.6f}, {gps_route[-1][1]:.6f})"
)


VehId disponibles en el dataset:
[10, 455, 541]

Trips disponibles para el VehId 455:
[554, 565, 568, 575, 588, 596, 600, 601, 603, 616, 625, 627, 630, 632, 635, 636, 646, 658, 659, 668, 669, 674, 678, 690, 694, 702, 719, 728, 735, 736, 738, 739, 755, 757, 772, 775, 778, 780, 787, 792, 795, 799, 803, 808, 816, 825, 869, 876, 883, 887, 896, 900, 901, 912, 915, 916, 936, 937, 941, 956, 960, 970, 982, 983, 986, 989, 1001, 1006, 1009, 1026, 1034, 1035, 1049, 1064, 1067, 1070, 1073, 1075, 1076, 1083, 1100, 1108, 1110, 1111, 1113, 1117, 1139, 1143, 1149, 1154, 1160, 1168, 1175, 1179, 1184, 1197, 1198, 1204, 1212, 1221, 1222, 1243, 1245, 1261, 1262, 1263, 1292, 1304, 1306, 1310, 1320, 1323, 1338, 1339, 1340, 1360, 1363, 1373, 1380, 1383, 1384, 1402, 1405, 1406, 1409, 1410, 1413, 1418, 1421, 1424, 1427, 1429, 1435, 1453, 1457, 1461, 1469, 1474, 1492, 1493, 1496, 1509, 1510, 1511, 1516, 1520, 1522, 1528, 1531, 1532, 1533, 1553, 1561, 1562, 1567, 1573, 1575, 1582, 1586, 1589, 1591, 1593, 1594, 

In [3]:
extractor = RouteFeatureExtractor(gps_route, weather_api_key="67a922066b844919a0a191058252705")
df_segments = extractor.run_all()

In [4]:
df_segments.head(20)

segment_id  Hour  Trip_distance     Delta_d   Hum     Slope  primary  \
0            0  17.0      31.250228    0.000000  80.0  0.000000        0   
1            1  17.0     153.324564  133.586366  80.0  0.000000        0   
2            2  17.0     256.689403  119.527388  80.0  0.000000        0   
3            3  17.0     397.382697  121.150509  80.0  0.472920        0   
4            4  17.0     511.486887  111.804881  80.0  0.000000        0   
5            5  17.0     640.762511  116.933145  80.0  1.469640        0   
6            6  17.0     705.179839   95.262698  80.0  0.000000        0   
7            7  17.0     834.048778  107.738109  80.0  0.000000        0   
8            8  17.0     936.764143   95.276447  80.0  1.803495        0   
9            9  17.0    1049.035432  122.340671  80.0  0.000000        0   
10          10  17.0    1168.164825  120.383413  80.0  2.853304        0   
11          11  17.0    1269.541036  102.096969  80.0  1.122236        0   
12          12  17.0    1388.721466  116.247188  80.0  0.000000        0   
13          13  17.0    1501.566052  109.332301  80.0  0.000000        0   
14          14  17.0    1610.119679  113.964512  80.0 -2.512144        0   
15          15  17.0    1709.949280  113.347025  80.0  0.000000        0   
16          16  17.0    1839.955009  121.706680  80.0 -3.291759        0   
17          17  17.0    1967.631116  105.112020  80.0  0.000000        0   
18          18  17.0    2075.806102  129.514352  80.0  0.000000        0   
19          19  17.0    2188.349369  106.817799  80.0  0.000000        0   

    residential  secondary  crossing  tertiary  give_way  
0             1          0         0         0         0  
1             1          0         0         0         0  
2             1          0         0         0         0  
3             1          0         0         0         0  
4             1          0         0         0         0  
5             1          0         0         0         0  
6             1          0         0         0         0  
7             1          0         0         0         0  
8             1          0         0         0         0  
9             1          0         0         0         0  
10            1          0         0         0         0  
11            1          0         0         0         0  
12            1          0         0         0         0  
13            1          0         0         0         0  
14            1          0         0         0         0  
15            1          0         0         0         0  
16            1          0         0         0         0  
17            1          0         0         0         0  
18            1          0         0         0         0  
19            1          0         0         0         0

In [5]:
df_segments.tail(20)

segment_id  Hour  Trip_distance     Delta_d   Hum     Slope  primary  \
120         120  17.0   14124.899090  132.063929  80.0 -4.761346        0   
121         121  17.0   14264.737675  140.903211  80.0  0.000000        0   
122         122  17.0   14397.541051  129.485175  80.0  0.000000        0   
123         123  17.0   14516.656853  127.724298  80.0  0.000000        0   
124         124  17.0   14649.792766  125.032816  80.0  0.000000        0   
125         125  17.0   14777.835730  126.985771  80.0 -0.451189        0   
126         126  17.0   14896.028899  121.725203  80.0  0.000000        0   
127         127  17.0   15013.844357  111.094428  80.0 -3.605410        0   
128         128  17.0   15125.214031  112.740264  80.0  0.000000        0   
129         129  17.0   15240.866487  116.942863  80.0  0.000000        0   
130         130  17.0   15340.327527  115.687509  80.0  0.000000        0   
131         131  17.0   15443.690208   89.329170  80.0  0.000000        0   
132         132  17.0   15546.966840   94.432796  80.0  0.000000        0   
133         133  17.0   15684.694983  135.231279  80.0  0.000000        0   
134         134  17.0   15754.862266   86.323137  80.0  1.327235        0   
135         135  17.0   15870.309361  102.075790  80.0  0.000000        0   
136         136  17.0   15976.868234  111.420828  80.0  0.000000        0   
137         137  17.0   16079.224671   83.906668  80.0  0.000000        0   
138         138  17.0   16190.640442  114.587398  80.0  0.000000        0   
139         139  17.0   16266.529691   52.592806  80.0  0.000000        0   

     residential  secondary  crossing  tertiary  give_way  
120            0          1         0         0         0  
121            0          1         0         0         0  
122            0          1         0         0         0  
123            0          1         0         0         0  
124            0          1         0         0         0  
125            0          1         0         0         0  
126            0          1         0         0         0  
127            0          1         0         0         0  
128            0          1         0         0         0  
129            0          1         0         0         0  
130            0          1         0         0         0  
131            0          1         0         0         0  
132            0          1         0         0         0  
133            0          1         0         0         0  
134            0          1         0         0         0  
135            0          1         0         0         0  
136            0          1         0         0         0  
137            0          1         0         0         0  
138            0          1         0         0         0  
139            0          1         0         0         0

In [6]:
df_segments.to_csv(f"veh{vehid_sel}_trip{trip_sel}_features.csv", index=False)

In [7]:
import folium
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.colors as mcolors
from math import radians, sin, cos, sqrt, atan2

# ---------------------------------------------------------------
# 1 · Coordenadas válidas
# ---------------------------------------------------------------
trip_df = df_trip[
    df_trip["matched_latitude"].notna() &
    df_trip["matched_longitude"].notna()
].copy().reset_index(drop=True)

if len(trip_df) < 2:
    raise ValueError("El viaje no tiene suficientes puntos GPS válidos.")

# ---------------------------------------------------------------
# 2 · Distancias punto a punto
# ---------------------------------------------------------------
def haversine_m(lat1, lon1, lat2, lon2):
    R = 6371000.0
    lat1, lon1 = radians(lat1), radians(lon1)
    lat2, lon2 = radians(lat2), radians(lon2)

    dlat = lat2 - lat1
    dlon = lon2 - lon1

    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
    return 2 * R * atan2(sqrt(a), sqrt(1 - a))


delta_d = [0.0]
for i in range(1, len(trip_df)):
    delta_d.append(
        haversine_m(
            trip_df.loc[i - 1, "matched_latitude"],
            trip_df.loc[i - 1, "matched_longitude"],
            trip_df.loc[i, "matched_latitude"],
            trip_df.loc[i, "matched_longitude"],
        )
    )

trip_df["delta_d"] = delta_d
trip_df["cum_distance_m"] = np.cumsum(delta_d)

# ---------------------------------------------------------------
# 3 · Segmentación correcta (acumulativa)
# ---------------------------------------------------------------
segment_length = 100.0  # metros

segment_ids = []
current_segment = 0
accum = 0.0

for d in trip_df["delta_d"]:
    if accum >= segment_length:
        current_segment += 1
        accum = 0.0
    segment_ids.append(current_segment)
    accum += d

trip_df["segment_id"] = segment_ids

n_segments = trip_df["segment_id"].nunique()
print(f"Número de segmentos: {n_segments}")

# ---------------------------------------------------------------
# 4 · Mapa base
# ---------------------------------------------------------------
center = (
    trip_df["matched_latitude"].mean(),
    trip_df["matched_longitude"].mean()
)

m = folium.Map(location=center, zoom_start=13, tiles="OpenStreetMap")

# ---------------------------------------------------------------
# 5 · Dibujar segmentos (color por segmento)
# ---------------------------------------------------------------
cmap = plt.colormaps["tab20"]

for seg_id, group in trip_df.groupby("segment_id"):

    coords_seg = list(
        zip(group["matched_latitude"], group["matched_longitude"])
    )

    if len(coords_seg) < 2:
        continue

    color = mcolors.to_hex(cmap(seg_id % cmap.N))

    folium.PolyLine(
        coords_seg,
        color=color,
        weight=6,
        opacity=0.9,
        tooltip=f"Segmento {seg_id}"
    ).add_to(m)

# ---------------------------------------------------------------
# 6 · Puntos GPS (saltos grandes)
# ---------------------------------------------------------------
threshold_m = 300

for i, row in trip_df.iterrows():

    is_jump = row["delta_d"] > threshold_m

    folium.CircleMarker(
        location=(row["matched_latitude"], row["matched_longitude"]),
        radius=6 if is_jump else 4,
        color="red" if is_jump else "black",
        fill=True,
        fill_opacity=0.8,
        tooltip=(
            f"Idx: {i}<br>"
            f"Segmento: {row['segment_id']}<br>"
            f"Δdist: {row['delta_d']:.1f} m<br>"
            f"Dist acum: {row['cum_distance_m']:.1f} m"
        )
    ).add_to(m)

# ---------------------------------------------------------------
# 7 · Inicio y fin
# ---------------------------------------------------------------
folium.Marker(
    (trip_df.loc[0, "matched_latitude"], trip_df.loc[0, "matched_longitude"]),
    icon=folium.Icon(color="green", icon="play"),
    tooltip="Inicio"
).add_to(m)

folium.Marker(
    (trip_df.loc[len(trip_df)-1, "matched_latitude"],
     trip_df.loc[len(trip_df)-1, "matched_longitude"]),
    icon=folium.Icon(color="red", icon="stop"),
    tooltip="Fin"
).add_to(m)

m

Número de segmentos: 138
